In [1]:
import requests
import pandas as pd
from bs4 import BeautifulSoup
import re
import matplotlib.pyplot as plt
plt.rcdefaults()



/Users/seanm/opt/anaconda3/envs/SummerEnv/lib/python3.8/site-packages/requests/__init__.py:102: RequestsDependencyWarning: urllib3 (1.26.9) or chardet (5.0.0)/charset_normalizer (2.0.4) doesn't match a supported version!
  warnings.warn("urllib3 ({}) or chardet ({})/charset_normalizer ({}) doesn't match a supported "


In [2]:
submission_dict = {}
fighters = []

Much credit to CGRetriever on Github, who I copied most of this webscraper from. 

https://github.com/CGRetriever/BJJ_Submission_Analysis/blob/master/BJJSubAnalyzer.py



In [3]:
def submission_counter(submission, increment):
    # Making sure the increment variable is an int
    increment = int(increment)

    # This will attempt to increment the counter for the submission. If the submission does not exist then it will
    # add it to the dictionary instead (via the except loop)
    try:
        submission_dict[submission] += int(increment)
    except KeyError:
        submission_dict[submission] = int(increment)

In [7]:
def get_fighters():
    # This will be grab the information from the bjjheroes website so that we can parse it
    page = requests.get(
        "https://www.bjjheroes.com/a-z-bjj-fighters-list")
    fighter_soup = BeautifulSoup(page.content, 'html.parser')

    # Search through the html for the first and last name of the fighters
    fighters_first_name = fighter_soup.find_all("td", class_='column-1')
    fighters_last_name = fighter_soup.find_all("td", class_='column-2')

    # Weird ass regex stuff. I don't understand it, I just copy and pasted this
    marker1 = ">"
    marker2 = "<"
    regexExpression = marker1 + '(.+?)' + marker2

    # This for loop is to create a full name for each fighter so that we can query the URLs with
    # each fighter's name
    for i, x in zip(fighters_first_name, fighters_last_name):
        tempFirst = str(i)
        tempLast = str(x)

        firstString = re.search(regexExpression, tempFirst).group(1)
        firstString = firstString.split(">")

        lastString = re.search(regexExpression, tempLast).group(1)
        lastString = lastString.split(">")
        fullname = firstString[1] + "-" + lastString[1]
        print(fullname)
        fighters.append(fullname)
        web_scrape(fullname)


In [6]:
def web_scrape(fighter):
    # This sets up the intial request to the site that we want to pull data from
    page = requests.get(
        "https://www.bjjheroes.com/bjj-fighters/" + fighter)
    soup = BeautifulSoup(page.content, 'html.parser')

    # print(soup)

    submissions_html = soup.find_all("div", class_='text')
    submission_numbers = soup.find_all("div", class_='totalvalue')
    example = soup.find_all(id="donut_value")
    marker1 = ">"
    marker2 = "<"
    regexExpression = marker1 + '(.+?)' + marker2

    for i, x in zip(submissions_html, submission_numbers):
        tempSubStr = str(i)
        tempNumStr = str(x)
        submissionString = re.search(regexExpression, tempSubStr).group(1)
        numberString = re.search(regexExpression, tempNumStr).group(1)
        submission_counter(submissionString, numberString)

    print(submission_dict)

In [ ]:
def web_scrape2(fighter): #natt use this one
    # initial request
    page = requests.get(
        "https://www.bjjheroes.com/bjj-figthers/" + fighter)
    soup = BeautifulSoup(page.content, 'html.parser')

    print(soup)
    
    

In [8]:
get_fighters()

Aarae-Alexander
{}
Aaron-Johnson
{'Straight ankle lock': 16, 'Kneebar': 8, 'Toe hold': 3, 'Choke from back': 4, 'Inside heel hook': 5, 'Heel hook': 3, 'Violin armlock': 2, 'Submission': 2, 'Armbar': 3, 'Triangle armbar': 4, 'Triangle': 3, 'Mounted choke': 1, 'Armlock': 1, 'Kimura': 1, 'Straignt ankle lock': 1, 'Flying armbar': 1, 'Outside heel hook': 1, 'Estima lock': 1, 'Calf slicer': 2, 'Footlock': 1, 'Reverse triangle': 2, 'RNC': 3, 'Katagatame': 2, 'Choke': 2, 'Brabo choke': 1, 'Arm in Ezekiel': 1, 'Cross choke': 1, 'Arm in guillotine': 1, 'Botinha': 1}
Abdurakhman-Bilarov
{'Straight ankle lock': 16, 'Kneebar': 9, 'Toe hold': 3, 'Choke from back': 4, 'Inside heel hook': 5, 'Heel hook': 8, 'Violin armlock': 2, 'Submission': 2, 'Armbar': 5, 'Triangle armbar': 4, 'Triangle': 3, 'Mounted choke': 1, 'Armlock': 1, 'Kimura': 2, 'Straignt ankle lock': 1, 'Flying armbar': 1, 'Outside heel hook': 1, 'Estima lock': 1, 'Calf slicer': 2, 'Footlock': 1, 'Reverse triangle': 2, 'RNC': 6, 'Katagata

Let's just get on with the ELO system for now

Rating will be determined as follows

NewRating = OldRating + *k*(Actual Outcome - Expected Outcome)

Where *k* is a parameter that converts differences in actual vs. expected outcomes into changes in ratings


Let us define actual outcome in the set {0,1} as follows

Win via submission: 1
Win via margin of 8 or more points: 0.9
Win via margin of 6-7 points: 0.8
Win via margin of 3-5 points: 0.7
Win via margin of 2 or less points: 0.6
Draw: 0.5
Loss: 0

EXPECTED OUTCOME

Let us defined expected outcome as follows

E = 1/(1+10^((OpponentRating-OwnRating)/S))

All should be self-explanatory save for parameter *S*. *S* is a scaling parameter that determines how the ratings deficit manifests. We will test ratings on a variety of *S*

In [12]:
raw_data = pd.read_csv("bjjdata.csv")

In [13]:
raw_data.head()

Fighter            Opponent W/L            Method  \
0  Aaron "Tex" Johnson  Quentin Rosensweig   L  Inside heel hook   
1  Aaron "Tex" Johnson       Neiman Gracie   L               RNC   
2  Aaron "Tex" Johnson     Richie Martinez   L         Heel hook   
3  Aaron "Tex" Johnson        Leo Nogueira   L            Points   
4  Aaron "Tex" Johnson      Romulo Azevedo   L               NaN   

        Competition Weight Stage  Year  
0          Kakuto 5    ABS   SPF  2015  
1      NoGi Pan Ams   94KG    SF  2015  
2  Kakuto Challenge    ABS    SF  2015  
3   Atlanta W. Open   94KG    SF  2016  
4    UAEJJF NYC Pro   94KG    SF  2016

In [14]:
raw_data.loc[raw_data["Year"] == 2015]

Fighter            Opponent W/L               Method  \
0      Aaron "Tex" Johnson  Quentin Rosensweig   L     Inside heel hook   
1      Aaron "Tex" Johnson       Neiman Gracie   L                  RNC   
2      Aaron "Tex" Johnson     Richie Martinez   L            Heel hook   
67     Aaron "Tex" Johnson     Vitor Schlosser   W             Toe hold   
68     Aaron "Tex" Johnson      Ricardo Bastos   W  Straight ankle lock   
...                    ...                 ...  ..                  ...   
40334           Ilke Bulut     Herbert Estevao   W               Points   
40335           Ilke Bulut    Douglas Barcelos   W               Injury   
40336           Ilke Bulut         Szabo Gyula   W                  Adv   
40337           Ilke Bulut         Szabo Gyula   W                  Adv   
40338           Ilke Bulut      Gustavo Dantas   W                  Adv   

            Competition Weight Stage  Year  
0              Kakuto 5    ABS   SPF  2015  
1          NoGi Pan Ams   94KG    SF  2015  
2      Kakuto Challenge    ABS    SF  2015  
67       NY Summer Open   94KG    SF  2015  
68       NY Summer Open   94KG     F  2015  
...                 ...    ...   ...   ...  
40334    Madrid NoGi O.   73KG    SF  2015  
40335    Madrid NoGi O.   73KG     F  2015  
40336         London FO   76KG    4F  2015  
40337       London FNGO   73KG     F  2015  
40338       Zurich Open   76KG     F  2015  

[2604 rows x 8 columns]

In [ ]:
class Fighter():
    def __init__(self, k):
        self.ELO = 500
        self.wins = 0
        self.losses = 0
        self.matches = 0
        self.submissions = {}
        self.k = k
    
    def update_record(self, outcome, submission):
        self.matches +=1
        if outcome == 1:
            self.wins +=1
        else:
            self.losses +=1
        
        if submission not in list(self.submissions.keys()):
            temp = {submission: 1}
            self.submissions.update(temp)
            print("Added submission {submission} to dict")
        else:
            self.submissions[submission] = self.submissions[submission] + 1
            print("Added 1 to {submission} count")
    
    def update_ELO(self, opponent_ranking, actual_outcome, expected_outcome):
        new_elo = self.ELO + self.k(actual_outcome - expected_outcome)
        self.ELO = new_elo
    



1